In [2]:
!pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 kB 8.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 18.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 21.4 MB/s eta 0:00:00


In [3]:
from datasets import load_dataset

# 데이터 300개 제한
dataset = load_dataset("Multimodal-Fatima/OK-VQA_train", split='train[0:300]')

# 데이터 columns 선택
dataset = dataset.select_columns(['image', 'answers', 'question'])

# 답변을 ID로 매핑하고, ID를 답변으로 매핑합니다.
answers = dataset['answers']
unique_answers = list(set([ans for item in answers for ans in item]))
answer_to_id = {answer: idx for idx, answer in enumerate(unique_answers)}
id_to_answer = {idx: answer for answer, idx in answer_to_id.items()}

# 답변을 ID로 교체합니다.
for idx in range(len(dataset)):
    dataset['answers'][idx] = [answer_to_id[ans] for ans in dataset['answers'][idx]]

# 데이터셋 편평화
flattened_dataset = dataset.flatten()

dataset.features


Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/9009 [00:00<?, ? examples/s]

{'image': Image(decode=True, id=None),
 'answers': Sequence(feature=Value(dtype='string', id=None), length=-1, id=None),
 'question': Value(dtype='string', id=None)}

In [4]:
#finetuning할 모델 가져오기
from transformers import AutoProcessor, AutoModelForCausalLM

processor = AutoProcessor.from_pretrained("microsoft/git-base-vqav2")
model = AutoModelForCausalLM.from_pretrained("microsoft/git-base-vqav2")

preprocessor_config.json:   0%|          | 0.00/503 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/453 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/2.82k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/709M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/141 [00:00<?, ?B/s]

In [ ]:
from transformers import BertTokenizerFast

# 토크나이저 로드
tokenizer = BertTokenizerFast.from_pretrained("microsoft/git-base-vqav2")

train_texts = ["microsoft/git-base-vqav2"]
val_texts = ["microsoft/git-base-vqav2"]

# Tokenizing
train_encodings = tokenizer(train_texts, truncation=True, padding=True)
val_encodings = tokenizer(val_texts, truncation=True, padding=True)

# input_ids, attention_mask, token_type_ids 추출
train_input_ids = train_encodings['input_ids']
train_attention_mask = train_encodings['attention_mask']

In [9]:
!pip install transformers[torch]
!pip install accelerate -U


In [10]:
from torch.utils.data import DataLoader
from transformers import AutoModelForCausalLM, BertTokenizerFast, TrainingArguments

# 배치 크기 설정
batch_size = 8

# DataLoader 생성
dataloader = DataLoader(flattened_dataset, batch_size=batch_size)


# 모델 초기화
model = AutoModelForCausalLM.from_pretrained("microsoft/git-base-vqav2")

# 출력 레이블 수 설정
num_labels = len(id_to_answer)

# 레이블과 ID 간의 매핑 정의
model.config.id2label = id_to_answer
model.config.label2id = {label: i for i, label in id_to_answer.items()}

training_args = TrainingArguments(
    output_dir="./git-vqa-finetuned-on-ok-vqa",
    per_device_train_batch_size=8,
    num_train_epochs=20,
    logging_dir="./logs",
)



ImportError: ignored